# Table of Contents
* [Importing of PySpark Libraries](#importandread)
* [Statistics about dataset and Spark Dataframe Preview](#statsanddf)
* [Data Cleaning](#datac)
* [PySpark SQL Queries](#pysparksql)
    * [Preview of data in SQL tables format](#sqltbl)
    * [Top 10 Applications Ranked by Total Number of Reviews](#top10reviews)
    * [Top 10 Applications Ranked by Type (Paid or Free)](#top10type)
    * [Distribution of Applications Categories by Total Number of Installs](#distcat)
    * [Top Paid Applications](#toppaid)

## Importing of PySpark Libraries <a class="anchor" id="importandread"></a>

In [ ]:
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql.types import StructType, StructField, StringType, IntegerType
from pyspark.sql.functions import *

In [ ]:
df = spark.read.load('/FileStore/tables/googleplaystore.csv', format='csv',sep=',',header='true',escape='"',inferschema='true')

## Statistics about dataset and Spark Dataframe Preview <a class="anchor" id="statsanddf"></a>

In [ ]:
df.count()

Out[4]: 10841

In [ ]:
df.show()

+--------------------+--------------+------+-------+----+-----------+----+-----+--------------+--------------------+------------------+------------------+------------+
|                 App|      Category|Rating|Reviews|Size|   Installs|Type|Price|Content Rating|              Genres|      Last Updated|       Current Ver| Android Ver|
+--------------------+--------------+------+-------+----+-----------+----+-----+--------------+--------------------+------------------+------------------+------------+
|Photo Editor & Ca...|ART_AND_DESIGN|   4.1|    159| 19M|    10,000+|Free|    0|      Everyone|        Art & Design|   January 7, 2018|             1.0.0|4.0.3 and up|
| Coloring book moana|ART_AND_DESIGN|   3.9|    967| 14M|   500,000+|Free|    0|      Everyone|Art & Design;Pret...|  January 15, 2018|             2.0.0|4.0.3 and up|
|U Launcher Lite –...|ART_AND_DESIGN|   4.7|  87510|8.7M| 5,000,000+|Free|    0|      Everyone|        Art & Design|    August 1, 2018|             1.2.4|4.0.3 

In [ ]:
df.printSchema()

root
 |-- App: string (nullable = true)
 |-- Category: string (nullable = true)
 |-- Rating: double (nullable = true)
 |-- Reviews: string (nullable = true)
 |-- Size: string (nullable = true)
 |-- Installs: string (nullable = true)
 |-- Type: string (nullable = true)
 |-- Price: string (nullable = true)
 |-- Content Rating: string (nullable = true)
 |-- Genres: string (nullable = true)
 |-- Last Updated: string (nullable = true)
 |-- Current Ver: string (nullable = true)
 |-- Android Ver: string (nullable = true)



## Data Cleaning <a class="anchor" id="datac"></a>

In [ ]:
df = df.drop("size", "Content Rating", "Last Updated", "Android Ver", "Current Ver")

In [ ]:
df.show(5)

+--------------------+--------------+------+-------+-----------+----+-----+--------------------+
|                 App|      Category|Rating|Reviews|   Installs|Type|Price|              Genres|
+--------------------+--------------+------+-------+-----------+----+-----+--------------------+
|Photo Editor & Ca...|ART_AND_DESIGN|   4.1|    159|    10,000+|Free|    0|        Art & Design|
| Coloring book moana|ART_AND_DESIGN|   3.9|    967|   500,000+|Free|    0|Art & Design;Pret...|
|U Launcher Lite –...|ART_AND_DESIGN|   4.7|  87510| 5,000,000+|Free|    0|        Art & Design|
|Sketch - Draw & P...|ART_AND_DESIGN|   4.5| 215644|50,000,000+|Free|    0|        Art & Design|
|Pixel Draw - Numb...|ART_AND_DESIGN|   4.3|    967|   100,000+|Free|    0|Art & Design;Crea...|
+--------------------+--------------+------+-------+-----------+----+-----+--------------------+
only showing top 5 rows



In [ ]:
df.printSchema()

root
 |-- App: string (nullable = true)
 |-- Category: string (nullable = true)
 |-- Rating: double (nullable = true)
 |-- Reviews: string (nullable = true)
 |-- Installs: string (nullable = true)
 |-- Type: string (nullable = true)
 |-- Price: string (nullable = true)
 |-- Genres: string (nullable = true)



In [ ]:
from pyspark.sql.functions import regexp_replace, col
df = df.withColumn("Reviews",col("Reviews").cast(IntegerType()))\
    .withColumn("Installs",regexp_replace(col("Installs"),"[^0-9]",""))\
    .withColumn("Installs",col("Installs").cast(IntegerType()))\
    .withColumn("Price",regexp_replace(col("Price"),"[$]",""))\
    .withColumn("Price",col("Price").cast(IntegerType()))

In [ ]:
df.show(5)

+--------------------+--------------+------+-------+--------+----+-----+--------------------+
|                 App|      Category|Rating|Reviews|Installs|Type|Price|              Genres|
+--------------------+--------------+------+-------+--------+----+-----+--------------------+
|Photo Editor & Ca...|ART_AND_DESIGN|   4.1|    159|   10000|Free|    0|        Art & Design|
| Coloring book moana|ART_AND_DESIGN|   3.9|    967|  500000|Free|    0|Art & Design;Pret...|
|U Launcher Lite –...|ART_AND_DESIGN|   4.7|  87510| 5000000|Free|    0|        Art & Design|
|Sketch - Draw & P...|ART_AND_DESIGN|   4.5| 215644|50000000|Free|    0|        Art & Design|
|Pixel Draw - Numb...|ART_AND_DESIGN|   4.3|    967|  100000|Free|    0|Art & Design;Crea...|
+--------------------+--------------+------+-------+--------+----+-----+--------------------+
only showing top 5 rows



## PySpark SQL <a class="anchor" id="pysparksql"></a>

In [ ]:
df.createOrReplaceTempView("Apps")

### Preview of data in SQL tables format <a class="anchor" id="sqltbl"></a>

In [ ]:
%sql select * from Apps

App Category Rating Reviews Installs Type Price Genres Photo Editor & Candy Camera & Grid & ScrapBook ART_AND_DESIGN 4.1 159 10000 Free 0 Art & Design Coloring book moana ART_AND_DESIGN 3.9 967 500000 Free 0 Art & Design;Pretend Play U Launcher Lite – FREE Live Cool Themes, Hide Apps ART_AND_DESIGN 4.7 87510 5000000 Free 0 Art & Design Sketch - Draw & Paint ART_AND_DESIGN 4.5 215644 50000000 Free 0 Art & Design Pixel Draw - Number Art Coloring Book ART_AND_DESIGN 4.3 967 100000 Free 0 Art & Design;Creativity Paper flowers instructions ART_AND_DESIGN 4.4 167 50000 Free 0 Art & Design Smoke Effect Photo Maker - Smoke Editor ART_AND_DESIGN 3.8 178 50000 Free 0 Art & Design Infinite Painter ART_AND_DESIGN 4.1 36815 1000000 Free 0 Art & Design Garden Coloring Book ART_AND_DESIGN 4.4 13791 1000000 Free 0 Art & Design Kids Paint Free - Drawing Fun ART_AND_DESIGN 4.7 121 10000 Free 0 Art & Design;Creativity Text on Photo - Fonteee ART_AND_DESIGN 4.4 13880 1000000 Free 0 Art & Design Name Art Photo Editor - Focus n Filters ART_AND_DESIGN 4.4 8788 1000000 Free 0 Art & Design Tattoo Name On My Photo Editor ART_AND_DESIGN 4.2 44829 10000000 Free 0 Art & Design Mandala Coloring Book ART_AND_DESIGN 4.6 4326 100000 Free 0 Art & Design 3D Color Pixel by Number - Sandbox Art Coloring ART_AND_DESIGN 4.4 1518 100000 Free 0 Art & Design Learn To Draw Kawaii Characters ART_AND_DESIGN 3.2 55 5000 Free 0 Art & Design Photo Designer - Write your name with shapes ART_AND_DESIGN 4.7 3632 500000 Free 0 Art & Design 350 Diy Room Decor Ideas ART_AND_DESIGN 4.5 27 10000 Free 0 Art & Design FlipaClip - Cartoon animation ART_AND_DESIGN 4.3 194216 5000000 Free 0 Art & Design ibis Paint X ART_AND_DESIGN 4.6 224399 10000000 Free 0 Art & Design Logo Maker - Small Business ART_AND_DESIGN 4.0 450 100000 Free 0 Art & Design Boys Photo Editor - Six Pack & Men's Suit ART_AND_DESIGN 4.1 654 100000 Free 0 Art & Design Superheroes Wallpapers | 4K Backgrounds ART_AND_DESIGN 4.7 7699 500000 Free 0 Art & Design Mcqueen Coloring pages ART_AND_DESIGN NaN 61 100000 Free 0 Art & Design;Action & Adventure HD Mickey Minnie Wallpapers ART_AND_DESIGN 4.7 118 50000 Free 0 Art & Design Harley Quinn wallpapers HD ART_AND_DESIGN 4.8 192 10000 Free 0 Art & Design Colorfit - Drawing & Coloring ART_AND_DESIGN 4.7 20260 500000 Free 0 Art & Design;Creativity Animated Photo Editor ART_AND_DESIGN 4.1 203 100000 Free 0 Art & Design Pencil Sketch Drawing ART_AND_DESIGN 3.9 136 10000 Free 0 Art & Design Easy Realistic Drawing Tutorial ART_AND_DESIGN 4.1 223 100000 Free 0 Art & Design Pink Silver Bow Keyboard Theme ART_AND_DESIGN 4.2 1120 100000 Free 0 Art & Design Art Drawing Ideas ART_AND_DESIGN 4.1 227 50000 Free 0 Art & Design Anime Manga Coloring Book ART_AND_DESIGN 4.5 5035 100000 Free 0 Art & Design Easy Origami Ideas ART_AND_DESIGN 4.2 1015 100000 Free 0 Art & Design I Creative Idea ART_AND_DESIGN 4.7 353 10000 Free 0 Art & Design How to draw Ladybug and Cat Noir ART_AND_DESIGN 3.8 564 100000 Free 0 Art & Design UNICORN - Color By Number & Pixel Art Coloring ART_AND_DESIGN 4.7 8145 500000 Free 0 Art & Design;Creativity Floor Plan Creator ART_AND_DESIGN 4.1 36639 5000000 Free 0 Art & Design PIP Camera - PIP Collage Maker ART_AND_DESIGN 4.7 158 10000 Free 0 Art & Design How To Color Disney Princess - Coloring Pages ART_AND_DESIGN 4.0 591 500000 Free 0 Art & Design Drawing Clothes Fashion Ideas ART_AND_DESIGN 4.2 117 10000 Free 0 Art & Design Sad Poetry Photo Frames 2018 ART_AND_DESIGN 4.5 176 100000 Free 0 Art & Design Textgram - write on photos ART_AND_DESIGN 4.4 295221 10000000 Free 0 Art & Design Paint Splash! ART_AND_DESIGN 3.8 2206 100000 Free 0 Art & Design;Creativity Popsicle Sticks and Similar DIY Craft Ideas ART_AND_DESIGN 4.2 26 10000 Free 0 Art & Design Canva: Poster, banner, card maker & graphic design ART_AND_DESIGN 4.7 174531 10000000 Free 0 Art & Design Install images with music to make video without Net - 2018 ART_AND_DESIGN 4.6 1070 100000 Free 0 Art & Design Little Teddy 

### Top 10 Applications Ranked by Total Number of Reviews <a class="anchor" id="top10reviews"></a>

In [ ]:
%sql select App,sum(Reviews) from Apps
group by 1
order by 2 desc
limit 10

App sum(Reviews) Instagram 266241989 WhatsApp Messenger 207348304 Clash of Clans 179558781 Messenger – Text and Video Chat for Free 169932272 Subway Surfers 166331958 Candy Crush Saga 156993136 Facebook 156286514 8 Ball Pool 99386198 Clash Royale 92530298 Snapchat 68045010

Databricks visualization. Run in Databricks to view.

### Top 10 Applications Ranked by Type (Paid or Free) <a class="anchor" id="top10type"></a>

In [ ]:
%sql select App,Type,sum(Installs) from Apps
group by 1,2
order by 3 desc

App Type sum(Installs) Subway Surfers Free 6000000000 Instagram Free 4000000000 Google Drive Free 4000000000 Hangouts Free 4000000000 Google Photos Free 4000000000 Google News Free 4000000000 Candy Crush Saga Free 3500000000 WhatsApp Messenger Free 3000000000 Gmail Free 3000000000 Temple Run 2 Free 3000000000 Skype - free IM & video calls Free 3000000000 Google Chrome: Fast & Secure Free 3000000000 Messenger – Text and Video Chat for Free Free 3000000000 Maps - Navigate & Explore Free 3000000000 Viber Messenger Free 2500000000 Snapchat Free 2000000000 Google Street View Free 2000000000 Pou Free 2000000000 Facebook Free 2000000000 YouTube Free 2000000000 imo free video calls and chat Free 2000000000 Google+ Free 2000000000 Google Play Games Free 2000000000 Google Free 2000000000 LINE: Free Calls & Messages Free 1500000000 UC Browser - Fast Download Private & Secure Free 1500000000 Dropbox Free 1500000000 Flipboard: News For Our Time Free 1500000000 MX Player Free 1500000000 Microsoft Word Free 1500000000 Twitter Free 1500000000 Gboard - the Google Keyboard Free 1500000000 My Talking Tom Free 1500000000 Google Calendar Free 1500000000 Google Translate Free 1000000000 Google Duo - High Quality Video Calls Free 1000000000 Google Play Books Free 1000000000 Google Play Movies & TV Free 1000000000 SHAREit - Transfer & Share Free 1000000000 Facebook Lite Free 1000000000 ROBLOX Free 900000000 Duolingo: Learn Languages Free Free 700000000 8 Ball Pool Free 700000000 Sniper 3D Gun Shooter: Free Shooting Games - FPS Free 600000000 Helix Jump Free 600000000 slither.io Free 600000000 TripAdvisor Hotels Flights Restaurants Attractions Free 500000000 eBay: Buy & Sell this Summer - Discover Deals Now! Free 500000000 Angry Birds Classic Free 500000000 Samsung Health Free 500000000 Wish - Shopping Made Fun Free 500000000 Clean Master- Space Cleaner & Antivirus Free 500000000 Cloud Print Free 500000000 Security Master - Antivirus, VPN, AppLock, Booster Free 500000000 Netflix Free 500000000 Plants vs. Zombies FREE Free 500000000 Flow Free Free 500000000 Farm Heroes Saga Free 500000000 BeautyPlus - Easy Photo Editor & Selfie Camera Free 500000000 Zombie Tsunami Free 500000000 Clash Royale Free 400000000 Talking Tom Gold Run Free 400000000 Evernote – Organizer, Planner for Notes & Memos Free 400000000 Angry Birds Rio Free 400000000 Minion Rush: Despicable Me Official Game Free 400000000 Badoo - Free Chat & Dating App Free 400000000 Google Keep Free 400000000 Garena Free Fire Free 400000000 AliExpress - Smarter Shopping, Better Living Free 400000000 ZEDGE™ Ringtones & Wallpapers Free 400000000 WeChat Free 400000000 My Talking Angela Free 400000000 Google Pay Free 400000000 Clash of Clans Free 400000000 Hill Climb Racing Free 400000000 Cymera Camera- Photo Editor, Filter,Collage,Layout Free 400000000 Bowmasters Free 300000000 Google Docs Free 300000000 Candy Camera - selfie, beauty camera, photo editor Free 300000000 Score! Hero Free 300000000 Pinterest Free 300000000 KakaoTalk: Free Calls & Text Free 300000000 Microsoft OneNote Free 300000000 B612 - Beauty & Filter Camera Free 300000000 Dream League Soccer 2018 Free 300000000 Candy Crush Soda Saga Free 300000000 Opera Mini - fast web browser Free 300000000 IMDb Movies & TV Free 300000000 Amazon Shopping Free 300000000 Tumblr Free 300000000 Hungry Shark Evolution Free 300000000 Firefox Browser fast & private Free 300000000 Yahoo Mail – Stay Organized Free 300000000 Opera Browser: Fast and Secure Free 300000000 Camera360: Selfie Photo Editor with Funny Sticker Free 300000000 UC Browser Mini -Tiny Fast Private & Secure Free 300000000 Telegram Free 300000000 Cut the Rope FULL FREE Free 300000000 YouCam Perfect - Selfie Photo Editor Free 300000000 Adobe Acrobat Reader Free 300000000 ES File Explorer File Manager Free 300000000 Booking.com Travel Deals Free 300000000 Calorie Counter - MyFitnessPal Free 250000000 MeetMe: Chat & Meet New People Free 250000000 Granny Free 250000000 Who Free 200000000 GO Keyboa

### Distribution of Applications Categories by Total Number of Installs <a class="anchor" id="distcat"></a>

In [ ]:
%sql select Category,sum(Installs) from Apps
group by 1
order by 2 desc

Category sum(Installs) GAME 35086024415 COMMUNICATION 32647276251 PRODUCTIVITY 14176091369 SOCIAL 14069867902 TOOLS 11452771915 FAMILY 10258263505 PHOTOGRAPHY 10088247655 NEWS_AND_MAGAZINES 7496317760 TRAVEL_AND_LOCAL 6868887146 VIDEO_PLAYERS 6222002720 SHOPPING 3247848785 ENTERTAINMENT 2869160000 PERSONALIZATION 2325494782 BOOKS_AND_REFERENCE 1921469576 SPORTS 1751174498 HEALTH_AND_FITNESS 1583072512 BUSINESS 1001914865 FINANCE 876648734 EDUCATION 871452000 MAPS_AND_NAVIGATION 724281890 LIFESTYLE 537643539 WEATHER 426100520 FOOD_AND_DRINK 273898751 DATING 264310807 HOUSE_AND_HOME 168712461 ART_AND_DESIGN 124338100 LIBRARIES_AND_DEMO 62995910 COMICS 56086150 MEDICAL 53257437 AUTO_AND_VEHICLES 53130211 PARENTING 31521110 BEAUTY 27197050 EVENTS 15973161 1.9 null

### Top Paid Applications <a class="anchor" id="toppaid"></a>

In [ ]:
%sql select App,sum(Price) from Apps
where Type='Paid'
group by 1
order by 2 desc

App sum(Price) I'm Rich - Trump Edition 400 I am Rich Plus 399 I AM RICH PRO PLUS 399 I'm Rich/Eu sou Rico/أنا غني/我很有錢 399 I Am Rich Premium 399 most expensive app (H) 399 I Am Rich Pro 399 I am rich(premium) 399 I am Rich 399 I am Rich! 399 💎 I'm rich 399 I am rich (Most expensive app) 399 I am rich 399 Eu Sou Rico 394 I Am Rich 389 I am extremely Rich 379 I am rich VIP 299 EP Cook Book 200 Vargo Anesthesia Mega App 158 cronometra-br 154 BP Fitness Lead Scanner 109 Lean EQ 89 Language Therapy: Aphasia 74 Human Anatomy Atlas 2018: Complete 3D Human Body 72 A Manual of Acupuncture 66 EMT PASS 58 PTA Content Master 58 Advanced Comprehension Therapy 48 Muscle Premium - Human Anatomy, Kinesiology, Bones 48 Dr.Dice - Sic bo analyzer 46 Norwegian For Kids & Babies F 39 LTC AS Legal 39 Hospitalist Handbook 38 I am Rich Person 37 2017 EMRA Antibiotic Guide 32 Eu sou Rico 30 Golfshot Plus: Golf GPS 29 AP Art History Flashcards 29 Guide to Nikon Df 29 Dz kayas 28 AnatomyMapp 28 Block Buddy 28 G-NetReport Pro 25 Cardiac diagnosis (heart rate, arrhythmia) 24 Essential Anatomy 3 22 EMT Review Plus 22 Paramedic Protocol Provider 20 DRAGON QUEST VIII 19 AW Toolbox 19 USMLE Step 2 CK Flashcards 19 boattheory.ch Full 2018 19 Z PIVOT 19 NewTek NDI 19 ASCCP Mobile 18 Monash Uni Low FODMAP Diet 18 Diabetes & Diet Tracker 18 I am Rich Premium Plus 18 The World Ends With You 17 SkyTest BU/GU Lite 17 Trine 2: Complete Story 16 Facetune - For Free 15 Navi Radiography Pro 15 Interactive CT and MRI Anatomy 15 Electrician Calculator Pro 14 DRAGON QUEST V 14 G-NetTrack Pro 14 DRAGON QUEST VI 14 DRAGON QUEST IV 14 Chess of Blades (BL/Yaoi Game) (No VA) 14 Number Therapy 14 Blackjack Verite Drills 14 Ak Parti Yardım Toplama 13 FINAL FANTASY DIMENSIONS 13 Minecraft 12 ZombieVital DG 12 Carrier Landings Pro 12 DS Helpdesk Plus 12 Journal Club: Medicine 12 BackCountry Navigator TOPO GPS PRO 11 Medical ID - In Case of Emergency (ICE) 10 go41cx 10 CCHT PREP 10 Pedi STAT 10 RPG ブレイジング ソウルズ アクセレイト 10 Fuzzy Numbers: Pre-K Number Foundation 10 XCOM®: Enemy Within 9 FORD V SERIES CALC - NO LIMIT 9 Dr. Panda & Toto's Treehouse 9 Star Wars ™: DIRTY 9 Vital Tones EI Pro 9 Baldur's Gate: Enhanced Edition 9 BIG Launcher 9 Jeppesen CR Flight Computer 9 EF Lens Simulator 9 500 AP World History Questions 9 DRAGON QUEST III 9 Pocket AC 9 Chest CT Sectional Walker 9 Critical Care Paramedic Review 9 InfantRisk Center HCP 9 Abdominal CT Sectional Walker 9 Baldur's Gate II 9 CHRONO TRIGGER (Upgrade Ver.) 9 ACCDB MDB DB Manager Pro - Editor for MS Access 8 Football Manager Mobile 2018 8 USB BT Wi-Fi Color Terminal Modem 8 Maps & GPS Navigation OsmAnd+ 8 MC.Fitting 8 TurboScan: scan documents and receipts in PDF 8 Greater London A-Z 2016 8 Tiny Scanner Pro: PDF Doc Scan 8 DG Surveyor 8 My Movies Pro - Movie & TV Collection Library 7 Police Field Interview FI Card 7 Backgammon NJ for Android 7 FINAL FANTASY V 7 Children Educational Game Full 7 Fast Tract Diet 7 AMBW Dating App: Asian Men Black Women Interracial 7 Recognise Foot 7 Acupuncture Assistant 7 Ad Removal: thereisonlywe 6 FN model 1900 pistol explained 6 New York Mysteries (Full) 6 FN FAL rifle explained 6 The EO Bar 6 Toca Life: City 6 Moco+ - Chat, Meet People 6 Prime Key for Nougat Launcher& O Launcher &KitKat 6 Radiological Anatomy For FRCR1 6 Call of Duty:Black Ops Zombies 6 Florida Tides & Weather 6 Sago Mini Babies 6 FN pistol model 1903 explained 6 The Legacy (Full) 6 Grand Theft Auto: San Andreas 6 EMT Tutor NREMT-B Study Guide 6 The FN HP pistol explained 6 Calculator 6 Camera FV-5 6 AF-STROKE 5 Campervan.Guide Pro 5 bpresso PRO 5 CZ-27 pistol explained 5 BSPlayer 5 aCalendar+ Calendar & Tasks 5 amm dz 5 CZ-38 (vz 38) pistol explained 5 CZ-Cyberon Voice Commander 5 Pistolet CZ-70 CZ-50 expliqué 5 CZ-45 pistol explained 5 Weather Live 5 KeePass DX Pro 5 Pistolet FN GP35 expliqué 5 RollerCoaster Tycoon® Classic 5 OrthoFlow 5 Please Don't Touch Anything 3D 5 OptoDrum 5 BG Monitor Diabetes Pro 5 CZ-70 (CZ-50) pistol